## Prametri di cluster rispetto al tempo

In [1]:
import pickle
import pandas as pd
import glob2
import plotly.express as px
import plotly.graph_objects as go
from influxdb import InfluxDBClient

from plotly.subplots import make_subplots
import log_loader_time

Welcome to JupyROOT 6.16/00


In [2]:
savefilename="/media/alb/Removibile/graal_extract/cluster_dataframe"
with open (savefilename,"rb+") as savefile:
    cluster_pd=pickle.load(savefile)  

In [3]:
cluster_pd['time'] = pd.to_datetime(cluster_pd['time'],unit='s')
cluster_pd=cluster_pd.set_index("time")
cluster_pd["hour"]=cluster_pd.index.hour
cluster_pd["day"]=cluster_pd.index.date


Per ridurre il numero di plot, ho mediato le statistiche fra top e bottom

In [4]:
cluster_pd["Cluster_charge_L1_X"]=(cluster_pd["Cluster_charge_L1top_spX"]+cluster_pd["Cluster_charge_L1bot_spX"])/2
cluster_pd["Cluster_charge_L2_X"]=(cluster_pd["Cluster_charge_L2top_spX"]+cluster_pd["Cluster_charge_L2bot_spX"])/2
cluster_pd["Cluster_charge_L1_V"]=(cluster_pd["Cluster_charge_L1top_spV"]+cluster_pd["Cluster_charge_L1bot_spV"])/2
cluster_pd["Cluster_charge_L2_V"]=(cluster_pd["Cluster_charge_L2top_spV"]+cluster_pd["Cluster_charge_L2bot_spV"])/2

cluster_pd["Cluster_size_L1_X"]=(cluster_pd["Cluster_size_L1top_spX"]+cluster_pd["Cluster_size_L1bot_spX"])/2
cluster_pd["Cluster_size_L2_X"]=(cluster_pd["Cluster_size_L2top_spX"]+cluster_pd["Cluster_size_L2bot_spX"])/2
cluster_pd["Cluster_size_L1_V"]=(cluster_pd["Cluster_size_L1top_spV"]+cluster_pd["Cluster_size_L1bot_spV"])/2
cluster_pd["Cluster_size_L2_V"]=(cluster_pd["Cluster_size_L2top_spV"]+cluster_pd["Cluster_size_L2bot_spV"])/2


In [5]:
cluster_pd_res=cluster_pd.resample("7200s").mean()

In [6]:
def plot_parameter_by_time(param):
    fig=px.scatter(x=cluster_pd_res.index,y=cluster_pd_res[param],color=cluster_pd_res.run.astype('str'))
    fig.update_xaxes(title="Time")
    if "charge" in param:
        title= param + " [fC] (avg 2h)"
    else:
        title= param + " (avg 2h)"

    fig.update_yaxes(title=title)
    fig.add_shape(
        # Line Vertical
        dict(
            type="line",
            yref="paper",
            x0="2020-06-23 12:00:00",
            y0=0,
            x1="2020-06-23 12:00:00",
            y1=1,
            line=dict(
                color="LightSeaGreen",
                width=1,
                dash="dashdot"
            )
    ))
    fig.add_shape(
        # Line Vertical
        dict(
            type="line",
            yref="paper",
            x0="2020-04-09 12:00:00",
            y0=0,
            x1="2020-04-09 12:00:00",
            y1=1,
            line=dict(
                color="LightSeaGreen",
                width=1,
                dash="dashdot"
            )
    ))
    fig.add_shape(
        # Line Vertical
        dict(
            type="line",
            yref="paper",
            x0="2020-02-06 12:00:00",
            y0=0,
            x1="2020-02-06 12:00:00",
            y1=1,
            line=dict(
                color="LightSeaGreen",
                width=1,
                dash="dashdot"
            )
    ))
    fig.show()

Seguono i plot rispetto al tempo delle varie performace di cluster. Le righe verticali rappresentano i cambi bombola

In [15]:
plot_parameter_by_time("Cluster_charge_L1_X")
plot_parameter_by_time("Cluster_charge_L1_V")
plot_parameter_by_time("Cluster_size_L1_X")
plot_parameter_by_time("Cluster_size_L1_V")
plot_parameter_by_time("Cluster_charge_L2_X")
plot_parameter_by_time("Cluster_charge_L2_V")
plot_parameter_by_time("Cluster_size_L2_X")
plot_parameter_by_time("Cluster_size_L2_V")


Nei plot sotto la visualizzaizone dei paramentri di H e T durante i vari run. (solo per capire quando avevamo il datto e che run era in corso)

In [16]:
client = InfluxDBClient(host='localhost', port=8086)
client.get_list_database()
client.switch_database('GUFI_DB')
result=client.query('SELECT mean("Humidity") FROM "offline_data"."Environment" WHERE time > \'2020-01-01T00:00:00Z\' and time <\'2020-08-01T14:00:00Z\'  GROUP BY time(10m)',epoch='s')
points=result.get_points()
dict_4_pd={
    "time":[],
    "humidity":[]
}
for point in points:
    dict_4_pd["time"].append(point["time"]+28800)
#     if point["mean"]==None:
#             dict_4_pd["humidity"].append(0)
#     else:
#         dict_4_pd["humidity"].append(point["mean"])
    dict_4_pd["humidity"].append(point["mean"])
humidity_pd=pd.DataFrame(dict_4_pd)
humidity_pd['time']=pd.to_datetime(humidity_pd['time'],unit='s')
humidity_pd=humidity_pd.set_index("time")

In [17]:

client = InfluxDBClient(host='localhost', port=8086)
client.get_list_database()
client.switch_database('GUFI_DB')
result=client.query('SELECT mean("Temperature") FROM "offline_data"."Environment" WHERE time > \'2020-01-01T00:00:00Z\' and time <\'2020-08-01T14:00:00Z\'  GROUP BY time(20m)',epoch='s')
points=result.get_points()
dict_4_pd={
    "time":[],
    "temperature":[]
}
for point in points:
    dict_4_pd["time"].append(point["time"]+28800)
#     if point["mean"]==None:
#             dict_4_pd["humidity"].append(0)
#     else:
#         dict_4_pd["humidity"].append(point["mean"])
    dict_4_pd["temperature"].append(point["mean"])
temperature_pd=pd.DataFrame(dict_4_pd)
temperature_pd['time']=pd.to_datetime(temperature_pd['time'],unit='s')
temperature_pd=temperature_pd.set_index("time")

In [18]:
fig = make_subplots(specs=[[{"secondary_y": True}]])
cluster_pd_res["color_map"]= cluster_pd_res["run"].astype(str)
fig.add_trace( 
    go.Scatter(x=cluster_pd_res.index,
               y=cluster_pd_res.Cluster_charge_L2top_spX,
              mode="markers",
               name="Cluster_charge_L2top_spX",
                 text=cluster_pd_res.run,
               hovertemplate=
               'Run: %{text}'+'<br><b>Cluster_charge_L2top_spX</b>: %{y}',
               marker=dict(
                size=3,
                color=cluster_pd_res.run,
                   colorscale= px.colors.qualitative.G10
              )))

fig.add_trace( 
    go.Scatter(x=humidity_pd.index,y=humidity_pd.humidity,
              mode="lines",name="humidity"
              ),
    secondary_y=True)


# fig.add_trace( 
#     go.Scatter(x=temperature_pd.index,y=temperature_pd.temperature,
#               mode="lines",name="temperature"
#               ),
#     secondary_y=True)

fig.update_layout(title=dict(text='Cluster_charge_L2top_spX', x=0.5),
                   yaxis_title='Cluster_charge_L2top_spX',
                   yaxis2_title='Humidity',
                   xaxis_title='Time')
fig.show()

In [19]:
fig = make_subplots(specs=[[{"secondary_y": True}]])
cluster_pd_res["color_map"]= cluster_pd_res["run"].astype(str)
fig.add_trace( 
    go.Scatter(x=cluster_pd_res.index,
               y=cluster_pd_res.Cluster_charge_L2top_spX,
              mode="markers",
               name="Cluster_charge_L2top_spX",
                 text=cluster_pd_res.run,
               hovertemplate=
               'Run: %{text}'+'<br><b>Cluster_charge_L2top_spX</b>: %{y}',
               marker=dict(
                size=3,
                color=cluster_pd_res.run,
                   colorscale= px.colors.qualitative.G10
              )))

fig.add_trace( 
    go.Scatter(x=humidity_pd.index,y=temperature_pd.temperature,
              mode="lines",name="Temperature"
              ),
    secondary_y=True)


# fig.add_trace( 
#     go.Scatter(x=temperature_pd.index,y=temperature_pd.temperature,
#               mode="lines",name="temperature"
#               ),
#     secondary_y=True)

fig.update_layout(title=dict(text='Cluster_charge_L2top_spX', x=0.5),
                   yaxis_title='Cluster_charge_L2top_spX',
                   yaxis2_title='Temperature',
                   xaxis_title='Time')
fig.show()